# Comparison of the hyperspectral and assay data

Now that we have cleaned the hyperspectral data (hyperspec.csv) (See `Section 0 - Data Cleaning`), we can begin to compare the hyperspectral data with the geochemical assay data (assay.csv).

For every drillhole, the assay file contains the `Hole_ID`, depth, the chemical composition of the sample (Fe, Fe2O3, P, S, SiO2, Al2O3, MnO, Mn, CaO, K2O, MgO, Na2O, TiO2) and the loss-on-ignition percentage.

The hyperspec file contains the `Hole_ID` of every drillhole, depth, the chemical composition of each sample (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn), the loss-on-ignition percentage and other information about the minerals in the sample.

The common data between these two files are the `Hole_ID`, the depth, the loss-on-ignition percentage, and most columns about chemical composition (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn).

The aim of this notebook is to compare the two files in order to find the common holes and compare the values in identical holes in order to assess lab results from the two different techniques (hyperspectral and XRF).

In [ ]:
import numpy as np
import pandas as pd
import geolime as geo
import seaborn as sns

Format Pandas display for clarity and readability

In [ ]:
pd.set_option("display.max_rows", 20)
pd.set_option("display.max_columns", 500)

We want to compare the `Hole_ID` of the assay and hyperspectral file to know if they have some drillholes in common.

First we need to import these data from `.csv` files.

## Merging Interval Files 

### Assay File reading and formatting

In [ ]:
assay = geo.datasets.load("rocklea_dome/assay.csv")
assay

Some columns have string values named LNR, replacing them with NaN values will allow comparisons with other numerical columns. Here the `dtype` function is used to discriminate columns with strings (`object`) against columns with numerical values only (`float64, int64`)

In [ ]:
assay.dtypes

We can then determine which columns contain the value LNR using the `eq` function.

In [ ]:
assay.eq("LNR").any()

A `replace` function is then used to replace LNR values with NaN values.

All columns which previously held LNR values are then set to numeric dtypes using the `.apply(pd.to_numeric)` function.

In [ ]:
assay.replace("LNR", np.nan, inplace=True)
assay[["P", "S", "TiO2", "LOI"]] = assay[["P", "S", "TiO2", "LOI"]].apply(pd.to_numeric)

### Hyperspec File reading

In [ ]:
hyperspec = pd.read_csv("../data/hyperspec.csv")
hyperspec

### Merge Preparation

The comparison of the two datasets require to have the list of the different `Hole_ID` of both files. These lists also need to be turned into sets in order to compare them.
The set type ensures there are no duplicate values, being useful here as `Hole_ID` are unique identifier.

In [ ]:
colonne_assay = set(assay["Hole_ID"])
colonne_hyperspec = set(hyperspec["Hole_ID"])

Now we have two sets containing the different drill core Hole ID's that have been analyzed for each method. We can use the `len` method to determine how many Hole_ID values exist in each dataset.

In [ ]:
len(colonne_assay)

In [ ]:
len(colonne_hyperspec)

So we see 500 values in the assay file, and 192 in the hyperspec file.

Next, we can compute the intersection between all the `Hole_ID` in the assay and hyperspec files, and determine how many exist in both.

In [ ]:
intersection = colonne_assay.intersection(colonne_hyperspec)

In [ ]:
len(intersection)

The intersection of these two files has the same length as the smallest set (192), so we can infer that every `Hole_ID` in the hyperspectral file also exists in the assay file.

Now we want to see if the common columns between these two files have the same values. First we need to filter the DataFrame of the assay file in order to keep only the `Hole_ID` that are in common with the hyperspectral file.

To do this, we can create a list of the common columns using the `intersection` set created earlier, then create a new DataFrame (`filtered_assay`) by filtering the assay file by Hole_IDs common to both files.

In [ ]:
intersection = list(intersection)
filtred_assay = assay[assay["Hole_ID"].isin(intersection)]
filtred_assay

The next operation will delete every sample of the assay file that is not in the hyperspectral file to guarantee that we have the exact same number of `Hole_ID` in both files.

First we define our final assay dataframe (`assay_final`), being created from a merge of the `hyperspec` file, with the `filtered_assay` file, on the `Hole_ID`, `From` and `To` columns.

Then, we sort the `assay_final` dataframe by the `Hole_ID`, and the `From` column, so that drillholes are organised in alphabetical order, and samples are increasing in depth.

In [ ]:
assay_final = hyperspec.merge(filtred_assay, on=["Hole_ID", "From", "To"], how="left")
assay_final.sort_values(by=["Hole_ID", "From"], inplace=True)
assay_final

Columns which exist in both the assay and hyperspec files which have the same name will be given a suffix `_x` or `_y`. For example, both files contain an Alumnium Oxide value (`Al2O3`). This will be renamed `Al2O3_x` and `Al2O3_y` in the final file.

### Merged Data Verification

This new file allows us to make a comparison between the data from the assay file (obtained by an XRF analysis) and the data from the hyperspectral analysis.

To do this, we can use another open source python library (seaborn (sns))

First we can compare the Fe weight percentage via a simple scatterplot:

In [ ]:
sns.scatterplot(data=assay_final, x="Fe", y="Fe_pct");

Most of the measures are similar for both methods. We can do the same for the Al2O3 weight percentage :

In [ ]:
sns.scatterplot(data=assay_final, x="Al2O3_x", y="Al2O3_y");

Here we also see a good correlation between the two dataset.

In [ ]:
assay_final.drop(columns=["Al2O3_y", "LOI_x", "LOI_y"], inplace=True)
assay_final.rename(columns={"Al2O3_x": "Al2O3"}, inplace=True)

In [ ]:
assay_final.to_csv("../data/assay_hyper.csv", index=False)